In [ ]:
import os
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt

%matplotlib inline

font = {'weight' : 'normal',
        'size'   : 12}
matplotlib.rc('font', **font)

In [ ]:
def rbe_wedenberg(dose, let, abx,q):
    """
    Wedenberg proton RBE model
    input parameters may be either numpy.array or scalars
    TODO: handle Cube() class directly
    :params dose: physical proton dose in [Gy]
    :params let: LETd in [keV/um] (protons only)
    :params abx: alpha_x / beta_x [Gy]
    :returns: RBE for the given parameters
    :ref: http://dx.doi.org/10.3109/0284186X.2012.705892
    """

    _apx = 1.000 + q * let / abx
    _sbpx = 1.0

    rbe = _rbe_apx(dose, _apx, _sbpx, abx)
    return rbe

In [ ]:
def _rbe_apx(dose, apx, sbpx, abx, dzero=0.0):
    """
    :params dose: proton dose      [Gy]
    :params apx: alpha_p / alpha_x [dimensionless] RBE_max = ap/ax when (dose -> 0 Gy)
    :params sbpx: beta_p / beta_x  [dimensionless] RBE_min = sqrt(bp/bx) when (dose -> inf Gy)
    :params abx: alpha_x / beta_x  [Gy]
    :params dzero: what to return in case of dose is zero (which would cause division by zero)
    """

    _rbe = 1.0 / (2.0 * dose)
    if hasattr(_rbe, '__iter__'):
        _rbe[_rbe == np.inf] = dzero
    else:
        if _rbe == np.inf:
            return dzero
    delta = abx * abx + 4. * abx * apx * dose + 4. * sbpx * sbpx * dose * dose
    delta *= (delta > 0)
    _rbe *= (np.sqrt(delta) - abx)
    return _rbe

In [ ]:
fname = os.path.join('tmp','distrib_q.h5')
q = pd.read_hdf(fname, 'q',columns=['q'])

In [ ]:
fname = os.path.join('data',"sobp_10mln")
dose = os.path.join(fname,'dose.dat')
let=os.path.join(fname,'dlet.dat')

In [ ]:
dozym = os.path.join('data','doz_sobp.xlsx')
df_dozym = pd.read_excel(dozym,names=['depth','dose','depth2','dose2'])

In [ ]:
df_dose=pd.read_table(dose,names=['z','dose','err'],sep='\s+')
df_let=pd.read_table(let,names=['z','let','err'],sep='\s+')

# RBE for q=0.434

In [ ]:
rbe= pd.DataFrame()
dose_max=df_dose.dose[df_dose.dose>0.95*df_dose.dose.max()].mean()
rbe["dose"]=df_dose['dose']*2/dose_max
rbe["let"]=df_let['let']
rbe["z"]=df_dose['z']

In [ ]:
#q=0.434 from Wedenberg 
rbe['rbe_wed'] = rbe_wedenberg(rbe.dose, rbe.let, 2.41, 0.434)

# RBE distribution

In [ ]:
dfr = (rbe.reset_index(inplace=False))

In [ ]:
#optional : n=q.size-1
n=1000-1

In [ ]:
dfr =dfr.append([dfr]*n)

In [ ]:
dfr=(dfr.reset_index(inplace=False))[['z','let', 'dose']]

In [ ]:
dfr=dfr.sort_values(by=['z', 'let','dose'])

In [ ]:
dfr.set_index(['z'],inplace=True) 

In [ ]:
for name, group in dfr.groupby('z'):

    dfr.loc[(name), "q"] = q.q.values[:n+1]


In [ ]:
for name, group in dfr.groupby('z'):
    DOSE=group.dose.values
    LET=group.let.values
    Q=group.q.values
    
    dfr.loc[(name), "rbe"] = rbe_wedenberg(DOSE, LET, 2.41, Q)


In [ ]:
dfr.reset_index(inplace=True)

# Biological Dose

In [ ]:
limit=df_dose.z[df_dose.dose<=df_dose.dose.max()*0.01].iloc[0]

In [ ]:
figure2_df= pd.DataFrame()

In [ ]:
figure2_df["Distance_cm"] = rbe.z
figure2_df["Ext_Model_median"] = dfr.groupby('z').rbe.median().values*rbe.dose
figure2_df["Wedenberg"] = rbe.rbe_wed*rbe.dose
figure2_df["Physical__Dose"] = rbe.dose
figure2_df["Dose_for_RBE_1_1"] = rbe.dose*1.1
figure2_df["Ext_Model_quantile10"] = dfr.groupby('z').rbe.quantile(0.1).values*rbe.dose
figure2_df["Ext_Model_quantile90"] = dfr.groupby('z').rbe.quantile(0.9).values*rbe.dose

In [ ]:
fig,ax = plt.subplots(figsize =(10,6))

ax.set_xlabel("Range [cm]")
ax.set_ylabel("Dose [Gy]")
ax.set_xlim(0,limit)

ax.plot(figure2_df.Distance_cm,figure2_df.Ext_Model_median,'b:',markersize=0.1, label= "Ext. model median value")

ax.plot(figure2_df.Distance_cm,figure2_df.Wedenberg, label = "Wedenberg model")
ax.plot(figure2_df.Distance_cm, figure2_df.Physical__Dose,'r.',markersize=0.7, label = "Physical Dose") 
ax.plot(figure2_df.Distance_cm, figure2_df.Dose_for_RBE_1_1,'g-.',markersize=0.1, label = "RBE=1.1") 

y1=figure2_df.Ext_Model_quantile10
y2=figure2_df.Ext_Model_quantile90

plt.ylim(0,4)
plt.xticks(np.arange(0, 10, 1.0))
ax.fill_between(rbe.z,y1,y2, where=y2 >y1, facecolor='r', alpha=0.1, label = "CI 90%-10%")

plt.grid()
plt.minorticks_on()
plt.grid(which='minor', linestyle=':', linewidth='0.2', color='black')

plt.rcParams['xtick.direction'] = 'in' 
plt.rcParams['ytick.direction'] = 'in' 
plt.rcParams['xtick.top'] = True 
plt.rcParams['ytick.right'] = True
plt. legend(loc="upper left")
plt.savefig(fname="Biological Dose",dpi= 700, quality=95)

In [ ]:
figure2_df.to_csv("Biological_Dose_data")